In [7]:
import http.client
import json
import urllib.parse
import re
import pandas as pd
from shapely.geometry import Point, Polygon, MultiPolygon
import matplotlib.pyplot as plt
import numpy as np
import requests
import time
import os
import geopandas as gpd
from concurrent.futures import ThreadPoolExecutor, as_completed


In [8]:
# Function to parse the curl bash command into usable components
def clean_curl_request(curl_command):
    # Extract the URL
    url_pattern = r"curl '(.*?)'"
    match = re.search(url_pattern, curl_command)
    if match:
        url = match.group(1)
    else:
        raise ValueError("URL not found in the curl command")

    # Extract headers
    headers = {}
    header_pattern = r"-H '([^:]+): (.*?)'"
    for header_match in re.finditer(header_pattern, curl_command):
        header_name = header_match.group(1)
        header_value = header_match.group(2)
        headers[header_name] = header_value

    # Extract data
    data_pattern = r"--data-raw '(.*?)'"
    match = re.search(data_pattern, curl_command)
    data = {}
    if match:
        data_string = match.group(1)
        data_items = data_string.split("&")
        for item in data_items:
            key, value = item.split("=")
            data[key] = urllib.parse.unquote(value)

    # Parse URL for host and path
    parsed_url = urllib.parse.urlparse(url)
    host = parsed_url.netloc
    path = parsed_url.path + ("?" + parsed_url.query if parsed_url.query else "")

    return host, path, data, headers


In [9]:
def send_request(session, url, data, headers, lat, lng):
    # Update latitude and longitude in the data dictionary
    data["lat"] = str(lat)
    data["lng"] = str(lng)
    
    # Measure request time
    start_time = time.time()
    
    response = session.post(url, data=data, headers=headers)
    elapsed_time = time.time() - start_time  # Calculate elapsed time
    
    # Print the response time
    print(f"Response received in {elapsed_time:.2f} seconds for lat: {lat}, lng: {lng}")
    
    # Check for a successful response and return the result
    if response.status_code == 200:
        return response.json()
    else:
        print(f"Error: {response.status_code}, {response.text}")
        return None


In [10]:
import json
import numpy as np
import pandas as pd
from shapely.geometry import Polygon, Point

def load_geojson(filepath, ilce):
    """
    Opens up the source file and extracts the features for given district
    features: properties,id,name,geometry,geometry_type
    """
    with open(filepath, 'r', encoding='utf-8') as file:
        data = json.load(file)
    return [feature for feature in data["features"] if feature["properties"].get("name") == ilce] 


def extract_polygons(features):
    polygons = []
    for feature in features:
        geometry_type = feature["geometry"].get("type")  # Options: Polygon, MultiPolygon
        coordinates = feature["geometry"].get("coordinates")  # Polygon boundaries
        if geometry_type == "Polygon":
            if isinstance(coordinates, list) and len(coordinates) > 0:
                outer_ring = coordinates[0]  # The first element is the outer boundary
                polygons.append(Polygon(outer_ring))
        elif geometry_type == "MultiPolygon":
            for poly_coords in coordinates:
                if isinstance(poly_coords, list) and len(poly_coords) > 0:
                    outer_ring = poly_coords[0]  # The first element is the outer boundary
                    polygons.append(Polygon(outer_ring))
        else:
            raise ValueError(f"Unsupported geometry type: {geometry_type}")
    return polygons


def generate_grid(polygons, aralik):
    """
    This is not exactly a grid. We draw equally spaced lines on the polygon to divide it.
    Then we put dots on those lines where each of them are 100m's apart from each other.
    We use min-max lat-longs to determine our starting points.
    """
    red_points = [] # Points that are inside the polygons
    lat_spacing = aralik / 111320 # distance between two latitudes
    for polygon in polygons:
        min_lat = min(polygon.exterior.coords.xy[1]) 
        max_lat = max(polygon.exterior.coords.xy[1])
        lat_lines = np.arange(min_lat, max_lat, lat_spacing)
        for lat in lat_lines:
            min_lon = min(polygon.exterior.coords.xy[0]) 
            max_lon = max(polygon.exterior.coords.xy[0])
            lon_spacing = aralik / (111320 * np.cos(np.radians(lat)))
            lon_points = np.arange(min_lon, max_lon, lon_spacing)
            for lon in lon_points:
                point = Point(lon, lat)
                if any(polygon.contains(point) for polygon in polygons):
                    red_points.append((lon, lat))
    return red_points,polygons #We return the polygons but we don't need them anymore since we have the red points.


import pandas as pd
from shapely.geometry import Polygon, MultiPolygon
from concurrent.futures import ThreadPoolExecutor, as_completed

from shapely.geometry import Polygon, MultiPolygon
from concurrent.futures import ThreadPoolExecutor, as_completed
import pandas as pd

def process_api_requests(red_points, send_request_func, max_workers=10):
    columns = ["tesis_adi", "il_adi", "sokak_adi", "ilce_adi", "mahalle_adi", "lng", "lat", "id", "polygon_bounds"]
    rows = []
    
    with ThreadPoolExecutor(max_workers=max_workers) as executor:
        futures = {executor.submit(send_request_func, lat, lng): (lat, lng) for lng, lat in red_points}
        for future in as_completed(futures):
            lat, lng = futures[future]
            try:
                result = future.result()
                if isinstance(result, dict) and "features" in result:
                    for feature in result["features"]:
                        properties = feature["properties"]
                        coordinates = feature["geometry"].get("coordinates", [])
                        geom_type = feature["geometry"].get("type", "")

                        polygon_bounds = None
                        if geom_type == "Polygon" and coordinates:
                            try:
                                # Handle exterior and interior rings (holes)
                                exterior = coordinates[0]  # Outer ring
                                interiors = coordinates[1:]  # Inner rings (holes)
                                polygon_bounds = Polygon(exterior, interiors)
                            except Exception:
                                pass
                        elif geom_type == "MultiPolygon" and coordinates:
                            try:
                                polygons = []
                                for polygon_coords in coordinates:
                                    exterior = polygon_coords[0]  # Outer ring
                                    interiors = polygon_coords[1:]  # Inner rings (holes)
                                    polygons.append(Polygon(exterior, interiors))
                                polygon_bounds = MultiPolygon(polygons)
                            except Exception:
                                pass

                        row = {
                            "tesis_adi": properties.get("tesis_adi", ""),
                            "il_adi": properties.get("il_adi", ""),
                            "sokak_adi": properties.get("sokak_adi", ""),
                            "ilce_adi": properties.get("ilce_adi", ""),
                            "mahalle_adi": properties.get("mahalle_adi", ""),
                            "lng": lng,
                            "lat": lat,
                            "id": properties.get("id", ""),
                            "polygon_bounds": polygon_bounds.wkt if polygon_bounds else None,
                        }
                        rows.append(row)
            except Exception as e:
                print(f"Error processing point ({lat}, {lng}): {e}")
    
    df = pd.DataFrame(rows, columns=columns)
    return df.drop_duplicates(subset=["tesis_adi", "id"], keep='first')



 


def save_dataframe(df, filename):
    """
    Saves the given DataFrame to a CSV file.

    Args:
        df (pd.DataFrame): The DataFrame to save.
        filename (str): The name of the CSV file.
    """
    try:
        df.to_csv(filename, index=False, encoding='utf-8')
        print(f"Data saved successfully to {filename}")
    except Exception as e:
        print(f"An error occurred while saving the file: {e}")



def process_district(ilce, aralik, geojson_filepath, curl_command,id):
    # Parse the curl command
    host, path, data, headers = clean_curl_request(curl_command)
    url = f"https://{host}{path}"
    
    # Load GeoJSON and process data
    features = load_geojson(geojson_filepath, ilce)
    polygons = extract_polygons(features)
    red_points, polygons = generate_grid(polygons, aralik)  # Unpack both
    
    # Create a session and update headers
    session = requests.Session()
    session.headers.update(headers)
    
    # Define the function for API requests
    send_request_func = lambda lat, lng: send_request(session, url, data, headers, lat, lng)
    
    # Process API requests
    df = process_api_requests(red_points, send_request_func)  # Pass polygons explicitly
    print(df.head(10))
    
    # Save results
    save_dataframe(df, f"./new_results/{ilce}_{id}.csv")









In [11]:
# Example usage
curl_command = """
curl 'https://www.turkiye.gov.tr/afet-ve-acil-durum-yonetimi-acil-toplanma-alani-sorgulama?harita=goster&submit' \
  -H 'Accept: application/json, text/javascript, */*; q=0.01' \
  -H 'Accept-Language: en-US,en;q=0.9' \
  -H 'Connection: keep-alive' \
  -H 'Content-Type: application/x-www-form-urlencoded; charset=UTF-8' \
  -H 'Cookie: w3p=3352537280.20480.0000; _uid=1732219586-384a1de9-4e26-4ca2-ab3d-ea0c7ce3dd86; ridbb=WyI1ZWZjYWJjN2E5YzNiY2M4ZDY4OWExMGIwN2IwMTcyMmNjZDc5NjUzYyJd; language=tr_TR.UTF-8; TURKIYESESSIONID=hlc0aaikln36i3f3lhac5hjf90; TS015d3f68=015c1cbb6dd3827e877982af6b4c2f4bb9e542da8303dd008b3b018d6215dcf5722866d7a73626c6381e7c99f98a6f4952645c80f6; _lastptts=1738344819' \
  -H 'Origin: https://www.turkiye.gov.tr' \
  -H 'Referer: https://www.turkiye.gov.tr/afet-ve-acil-durum-yonetimi-acil-toplanma-alani-sorgulama?harita=goster' \
  -H 'Sec-Fetch-Dest: empty' \
  -H 'Sec-Fetch-Mode: cors' \
  -H 'Sec-Fetch-Site: same-origin' \
  -H 'User-Agent: Mozilla/5.0 (Macintosh; Intel Mac OS X 10_15_7) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/130.0.0.0 Safari/537.36 OPR/115.0.0.0' \
  -H 'X-Requested-With: XMLHttpRequest' \
  -H 'sec-ch-ua: "Chromium";v="130", "Opera";v="115", "Not?A_Brand";v="99"' \
  -H 'sec-ch-ua-mobile: ?0' \
  -H 'sec-ch-ua-platform: "macOS"' \
  --data-raw 'pn=%2Fafet-ve-acil-durum-yonetimi-acil-toplanma-alani-sorgulama&ajax=1&token=%7B2C7E6E-243446-CCFE96-0F6FFA-3D2A3E-514D47-D79C46-311AC8%7D&islem=getAlanlarForNokta&lat=39.80218353659573&lng=32.80429601669312'
"""
# Replace `send_request` with your actual API call function.
#process_district("Silivri", 100, "istanbul-admin-level-6.geojson", curl_command)

In [ ]:
with open('istanbul-admin-level-8-without-centers.geojson', 'r',encoding='utf-8') as file:
    data = json.load(file)

completed_neighborhoods = []

directory = os.fsencode('./new_results')
for file in os.listdir(directory):
    filename = os.fsdecode(file)
    if filename.endswith(".csv"): 
        completed_neighborhoods.append((os.path.splitext(os.path.basename(filename))[0]).split('.',1)[0])
        continue
    else:
        continue

for i in data["features"]:
    if i["properties"].get("name", "point") == 'point':
        continue
    else:
        ilce = i["properties"].get("name", "point")
        if ilce+'_'+i["properties"].get("@id").split('/')[-1] not in completed_neighborhoods:
            print(i["properties"].get("name", "point"))
            process_district(ilce, 100, "istanbul-admin-level-8-without-centers.geojson", curl_command,i["properties"].get("@id").split('/')[-1])
            completed_neighborhoods.append(ilce)
        else:
            print(i["properties"].get("name", "point"),': in results')
            continue

Kadıköy Mahallesi
Response received in 0.14 seconds for lat: 41.10332342234999, lng: 29.90756784739445
Response received in 0.14 seconds for lat: 41.102425111174995, lng: 29.914720454922897
Response received in 0.14 seconds for lat: 41.10332342234999, lng: 29.90995213687334
Response received in 0.14 seconds for lat: 41.10332342234999, lng: 29.911144281612785
Response received in 0.14 seconds for lat: 41.10332342234999, lng: 29.91233642635223
Response received in 0.15 seconds for lat: 41.102425111174995, lng: 29.912336198057535
Response received in 0.18 seconds for lat: 41.10332342234999, lng: 29.913528571091675
Response received in 0.05 seconds for lat: 41.10422173352498, lng: 29.908760171516388
Response received in 0.05 seconds for lat: 41.10422173352498, lng: 29.911144493610276
Response received in 0.05 seconds for lat: 41.10422173352498, lng: 29.9063758494225
Response received in 0.06 seconds for lat: 41.10332342234999, lng: 29.91472071583112
Response received in 0.06 seconds for la

In [ ]:
import os

# Directory containing the files
directory = "./new_results"

# Loop through files in the directory
for filename in os.listdir(directory):
    # Construct the full file path
    old_file_path = os.path.join(directory, filename)
    
    # Skip directories
    if os.path.isdir(old_file_path):
        continue
    
    # Create a new name for the file
    new_name = f"new_prefix_{filename}"
    new_file_path = os.path.join(directory, new_name)
    
    # Rename the file
    os.rename(old_file_path, new_file_path)
    print(f"Renamed: {filename} -> {new_name}")


In [ ]:
completed_neighborhoods

[]

In [ ]:
import json
with open('istanbul-admin-level-8-without-centers.geojson', 'r',encoding='utf-8') as file:
    data = json.load(file)

completed_neighborhoods = []

directory = os.fsencode('./new_results')
for file in os.listdir(directory):
    filename = os.fsdecode(file)
    if filename.endswith(".csv"): 
        completed_neighborhoods.append((os.path.splitext(os.path.basename(filename))[0]).split('.',1)[0])
        continue
    else:
        continue

In [8]:
completed_neighborhoods

['Bereketzade Mahallesi_7968240',
 'Aydınlı Mahallesi_8766077',
 'Paşaköy Mahallesi_1276035',
 'Kamiloba Mahallesi_9460117',
 'Çiftlik Mahallesi_9644018',
 'Batı Mahallesi_9218100',
 'Yıldıztabya Mahallesi_9381909',
 'Hacıahmet Mahallesi_8040978',
 'Kavaklı Ormanı_7666494',
 'Valide-i Atik Mahallesi_9463281',
 'Basınköy Mahallesi_7404512',
 'Duatepe Mahallesi_9321930',
 'Safa Mahallesi_9623102',
 'Esatpaşa Mahallesi_9397114',
 'Kanarya Mahallesi_7786491',
 'Ayazağa Mahallesi_9644506',
 'Poligon Mahallesi_9644555',
 'Kalem Mahallesi_8894466',
 'Çamçeşme Mahallesi_9219444',
 'Gültepe Mahallesi_7786484',
 'Sultan Selim Mahallesi_9362979',
 'Murat Çeşme Mahallesi_9460378',
 'Akat Mahallesi_9340899',
 'Rami Yeni Mahalle_9381765',
 'Kirazlı Mahallesi_9424884',
 'Mustafa Kemal Mahallesi_9397189',
 'Demirkapı Mahallesi_9424012',
 'Fındıklı Mahallesi_9441153',
 'Emniyetevleri Mahallesi_9363037',
 'Haraççı Mahallesi_9680772',
 'Çavuşoğlu Mahallesi_9286195',
 'Ağaçlı Mahallesi_9677587',
 'Karakir

In [ ]:
for file in os.listdir('./new_results'):
    print(file)

Bereketzade Mahallesi_7968240.csv
Aydınlı Mahallesi_8766077.csv
Paşaköy Mahallesi_1276035.csv
Kamiloba Mahallesi_9460117.csv
Çiftlik Mahallesi_9644018.csv
Batı Mahallesi_9218100.csv
Yıldıztabya Mahallesi_9381909.csv
Turgut Reis Mahallesi_9423121.csv
Hacıahmet Mahallesi_8040978.csv
Ahmet Yesevi Mahallesi_9042591.csv
Kavaklı Ormanı_7666494.csv
Hamidiye Mahallesi_9362930.csv
Valide-i Atik Mahallesi_9463281.csv
Basınköy Mahallesi_7404512.csv
Kemalpaşa Mahallesi_7786487.csv
Duatepe Mahallesi_9321930.csv
Atatürk Mahallesi_9642514.csv
Safa Mahallesi_9623102.csv
Esatpaşa Mahallesi_9397114.csv
Kanarya Mahallesi_7786491.csv
Ayazağa Mahallesi_9644506.csv
Poligon Mahallesi_9644555.csv
Kalem Mahallesi_8894466.csv
Çamçeşme Mahallesi_9219444.csv
İstiklal Mahallesi_9462868.csv
Gültepe Mahallesi_7786484.csv
Mehmet Akif Ersoy Mahallesi_9642969.csv
Sultan Selim Mahallesi_9362979.csv
Murat Çeşme Mahallesi_9460378.csv
Yeniköy Mahallesi_9644764.csv
Akat Mahallesi_9340899.csv
Rami Yeni Mahalle_9381765.csv
Ki